In [1]:
!pip3 install pandas

Defaulting to user installation because normal site-packages is not writeable
You should consider upgrading via the '/Library/Developer/CommandLineTools/usr/bin/python3 -m pip install --upgrade pip' command.


### Get the filelist

For the full results.json

In [2]:
import glob

# Specify the path to the folder containing the results.json files
folder_path = "lm-eval-output"

# Use glob to find all the results.json files
results_json_files = glob.glob(f"{folder_path}/**/results.json", recursive=True)

# Show total number of results.json files found
print(f"Found {len(results_json_files)} results.json files")


Found 6263 results.json files


### Process all the results.json

One file at a time

In [3]:
import json

# Global result map if it's not set
if 'global_result_map' not in globals():
    global_result_map = {}

#
# Function to process the results.json file
#
def process_results_json(file_path):
    with open(file_path) as f:
        data = json.load(f)

    # Model args, presplit by ','
    model_args = data['config']['model_args'].split(',')

    # Extract the pretrained value from config.model_args
    modelname = model_args[0].split('=')[1]

    # Opt array
    confArgsArr = model_args[1:]

    # Sort the opt array
    confArgsArr.sort()
    # Convert it to a string
    confStr = ','.join(confArgsArr)

    # Convert the option array of key=value strings to a dictionary
    confObj = { }
    for o in confArgsArr:
        k, v = o.split('=')
        confObj[k] = v
    
    # Create a dictionary to store the results, or use the existing one if it exists
    if modelname in global_result_map:
        modelObj = global_result_map[modelname]
    else:
        modelObj = {
            'name': modelname,
            'config': { }
        }
    
    # Get the opt object for the model
    if confStr in modelObj['config']:
        confSet = modelObj['config'][confStr]
    else:
        confSet = {
            'confStr': confStr,
            'confObj': confObj,
            'results': {},
            'groups': {}
        }

    # Iterate over the results and extract the result object for each test/group
    if 'results' in data:
        for test, result in data['results'].items():
            confSet['results'][test] = result
    if 'groups' in data:
        for test, result in data['groups'].items():
            confSet['groups'][test] = result
    
    # Update the global result map object
    modelObj['config'][confStr] = confSet
    global_result_map[modelname] = modelObj
    return modelObj

# Lets test the function with the first results.json file
first_result = process_results_json(results_json_files[0])
print(f"Processed example: ", first_result)


Processed example:  {'name': 'mistralai/Mistral-7B-Instruct-v0.2', 'config': {'dtype=bfloat16,trust_remote_code=True': {'confStr': 'dtype=bfloat16,trust_remote_code=True', 'confObj': {'dtype': 'bfloat16', 'trust_remote_code': 'True'}, 'results': {'cola': {'mcc,none': 0.12965656914783247, 'mcc_stderr,none': 0.032433640730190394, 'alias': 'cola'}}, 'groups': {}}}}


In [4]:
# Lets reset and reprocess all the results.json files
global_result_map = {}

# Process all the results.json files
for file in results_json_files:
    process_results_json(file)

# Show high level list of models
print(f"Found {len(global_result_map)} models")
print(f"Models: \n{list(global_result_map.keys())}")

# Save the result map to a file
with open('summary/compiled-lm-eval-results.json', 'w') as f:
    json.dump(global_result_map, f, sort_keys=True, indent='\t')

# Echo that its been saved to json
print(f"Saved to compiled-lm-eval-results.json")

Found 134 models
Models: 
['mistralai/Mistral-7B-Instruct-v0.2', 'mistralai/Mistral-7B-v0.1', 'mosaicml/mpt-7b-instruct', 'mosaicml/mpt-7b', 'mosaicml/mpt-7b-chat', 'bigscience/bloom-7b1', 'bigscience/bloomz-7b1-mt', 'bigscience/bloomz-7b1', 'EleutherAI/pythia-2.8b', 'EleutherAI/pythia-1.4b', 'EleutherAI/gpt-j-6b', 'EleutherAI/pythia-6.9b', 'google/flan-t5-base', 'google/gemma-2b', 'google/gemma-2b-it', 'google/gemma-7b', 'google/gemma-7b-it', 'google/flan-t5-large', 'microsoft/phi-1_5', 'microsoft/phi-2', 'microsoft/phi-1', 'allenai/OLMo-7B', 'TinyLlama/TinyLlama-1.1B-intermediate-step-1431k-3T', 'TinyLlama/TinyLlama-1.1B-Chat-v1.0', 'RWKV/rwkv-5-world-1b5', 'RWKV/rwkv-5-world-3b', 'RWKV/rwkv-4-world-3b', 'RWKV/v5-EagleX-v2-7B-HF', 'RWKV/rwkv-6-world-1b6', 'RWKV/rwkv-4-world-1b5', 'RWKV/v5-Eagle-7B-HF', 'RWKV/v6-Finch-7B-HF', 'RWKV/rwkv-6-world-3b-v2.1', 'RWKV/rwkv-4-world-7b', 'RWKV/v6-Finch-14B-HF', 'RWKV/rwkv-raven-7b', 'RWKV/rwkv-6-world-3b', 'aisingapore/sealion7b', 'aisingapore/

### Convert the results into CSV table formats

In [5]:
# Lets convert this into a table, which we will display in this notebook, and save as a CSV
import pandas as pd

##################################################
#
#  Utility functions
#
##################################################

# Check if the given name string, is within the list, including "*" wildcard
def is_in_list(name, list):
    for n in list:
        if n[-1] == '*':
            if name.startswith(n[:-1]):
                return True
        elif n == name:
            return True
    return False

# Is in inclusion exclusion list pair
def is_in_list_pair(name, inList, exList):
    if not is_in_list(name, inList):
        return False
    if is_in_list(name, exList):
        return False
    return True

# Prepare a single test/group result object
# By applying common filtering and formatting changes
def prepare_test_result(result):
    # The reutrn object
    ret = {}
    # Iterate the result key/value
    for k, v in result.items():
        # Skip if its alias
        if k == 'alias':
            continue

        # If the key ends with ",none", drop the ",none"
        if k.endswith(',none'):
            k = k[:-5]
        
        # Save the result
        ret[k] = v
    
    # Return the result
    return ret

##################################################
#
#  Generate the result
#
##################################################

# Create a list of rows for the table
def generate_result_table(
    inConfig = { "dtype": "bfloat16" },

    # Models to include/exclude
    inModels = ["*"],
    exModels = ["./rwkv-x-dev/*", "rwkv-x-dev"],

    # Results and groups to include
    inResults = [],
    inGroups = ["*"],

    # Exclude results and groups, applied after inResults and inGroups
    exResults = [],
    exGroups = [],

    # Sorted
    sort = False,
    simplified = False
):
    table_rows = []

    # Iterate over the models
    for model, modelObj in global_result_map.items():
        # Skip if not in the inModels or exModels
        if not is_in_list_pair(model, inModels, exModels):
            continue

        # Iterate over the configurations
        for confStr, confSet in modelObj['config'].items():
            # Get the confObj
            confObj = confSet['confObj']

            # Check if the inConfig, matches the confObj
            if inConfig:
                skip = False
                for k, v in inConfig.items():
                    if k not in confObj or confObj[k] != v:
                        skip = True
                        break
                if skip:
                    continue

            # Create a row object
            row = {
                'model': model,
                # 'config': confStr

                "avg_acc": 0.0,
                "avg_acc_stderr": 0.0,
            }

            # Total acc / acc_stderr
            acc_total = 0.0
            acc_count = 0
            acc_stderr_total = 0.0
            acc_stderr_count = 0

            # Add the groups
            for test, result in confSet['groups'].items():

                # Skip if not in the inGroups or exGroups
                if not is_in_list_pair(test, inGroups, exGroups):
                    continue

                # Filter the result obj
                cleanResult = prepare_test_result(result)

                # Add the result to the row, as seperate columns for each key
                for k, v in cleanResult.items():
                    if k == 'acc':
                        acc_total += v
                        acc_count += 1
                    elif k == 'acc_stderr':
                        acc_stderr_total += v
                        acc_stderr_count += 1
                    
                    # For simplified, we only use acc and perplexity
                    if simplified and k not in ['acc', 'perplexity']:
                        continue

                    # Save the value
                    row[f"{test} ({k})"] = v

            # Add the results
            for test, result in confSet['results'].items():

                # Skip if not in the inResults or exResults
                if not is_in_list_pair(test, inResults, exResults):
                    continue

                # Filter the result obj
                cleanResult = prepare_test_result(result)

                # Add the result to the row, as seperate columns for each key
                for k, v in cleanResult.items():
                    if k == 'acc':
                        acc_total += v
                        acc_count += 1
                    elif k == 'acc_stderr':
                        acc_stderr_total += v
                        acc_stderr_count += 1

                    # For simplified, we only use acc and perplexity
                    if simplified and k not in ['acc', 'perplexity']:
                        continue

                    # Save the value
                    row[f"{test} ({k})"] = v
                
            # Add the avg acc and acc_stderr
            if acc_count > 0:
               row["avg_acc"] = acc_total / acc_count
            if acc_stderr_count > 0:
                row["avg_acc_stderr"] = acc_stderr_total / acc_stderr_count

            # Append the row to the table
            table_rows.append(row)

    # Create a dataframe from the table rows
    df = pd.DataFrame(table_rows)

    # Sort by avg_acc
    if sort:
        df = df.sort_values(by='avg_acc', ascending=False)

    # Show the dataframe
    return df

# Generate the dataframe
df = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["xcopa"], inResults=[] )

# # Save the dataframe to a CSV file
# df.to_csv('summary/compiled-lm-eval-results.csv', index=False)

# Show results
df


/var/folders/71/91hw6kks41v97jkjp028xxbr0000gp/T/ipykernel_39274/788387412.py:2: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd


model   avg_acc  avg_acc_stderr  xcopa (acc)  \
0   mistralai/Mistral-7B-Instruct-v0.2  0.000000        0.000000          NaN   
1            mistralai/Mistral-7B-v0.1  0.559455        0.053879     0.559455   
2             mosaicml/mpt-7b-instruct  0.537091        0.041919     0.537091   
3                      mosaicml/mpt-7b  0.536000        0.042339     0.536000   
4                 mosaicml/mpt-7b-chat  0.538000        0.047059     0.538000   
..                                 ...       ...             ...          ...   
60                 huggyllama/llama-7b  0.541818        0.040718     0.541818   
61       meta-llama/Llama-2-7b-chat-hf  0.559818        0.054954     0.559818   
62            meta-llama/Llama-2-7b-hf  0.566727        0.052515     0.566727   
63          state-spaces/mamba-2.8b-hf  0.552909        0.035570     0.552909   
64          state-spaces/mamba-1.4b-hf  0.544182        0.031390     0.544182   

    xcopa (acc_stderr)  
0                  NaN  
1             0.053879  
2             0.041919  
3             0.042339  
4             0.047059  
..                 ...  
60            0.040718  
61            0.054954  
62            0.052515  
63            0.035570  
64            0.031390  

[65 rows x 5 columns]

In [6]:
##################################################
#
#  Build the various subsets
#
##################################################

FOCUS_MODEL_LIST=[
    # "./rwkv-x-dev/*", 
    "rwkv-x-dev/*", "RWKV/*", "meta-llama/Llama-2-7b*", "mistralai/Mistral-7B-v0.1", "m8than/*"
]

# Overall results
all_results = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=["*"] )
all_results.to_csv('summary/bf16-all-results-and-groups.csv', index=False)

all_results = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=["*"], simplified=True )
all_results.to_csv('summary/bf16-all-simplified-results-and-groups.csv', index=False)

all_results = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=["*"], simplified=True, sort=True )
all_results.to_csv('summary/bf16-all-sorted-results-and-groups.csv', index=False)

# Multilang results
multiLang_tTest = ["xcopa_*", "xnli_*", "xstorycloze_*", "xwinograd_*", "lambada_openai_*", "pawsx_*"]
multiLang_tGrps = ["xcopa",   "xnli",   "xstorycloze",   "xwinograd",   "lambada_multilingual", "pawsx"]
# Both test and groups, merged into a single list
multiLang_joint = multiLang_tTest + multiLang_tGrps

multilang_grp = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=multiLang_tGrps, inResults=[] )
multilang_test = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=multiLang_tGrps, inResults=multiLang_tTest )
multilang_grp.to_csv('summary/bf16-multilang-summary.csv', index=False)
multilang_test.to_csv('summary/bf16-multilang-results.csv', index=False)

multilang_grp_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=multiLang_tGrps, inResults=[], sort=True )
multilang_grp_sorted.to_csv('summary/bf16-sorted-multilang-summary.csv', index=False)

# RWKV perf tracking
rwkv_multilang_grp_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=multiLang_tGrps, inResults=[], exModels=[], inModels=FOCUS_MODEL_LIST, sort=True )
rwkv_multilang_grp_sorted.to_csv('summary/rwkv-x-dev-bf16-sorted-multilang-summary.csv', index=False)

# All other results
eng_grp = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=[], exGroups=multiLang_joint, exResults=multiLang_joint )
eng_grp_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=[], exGroups=multiLang_joint, exResults=multiLang_joint, sort=True )
eng_test = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=["*"], exGroups=multiLang_joint, exResults=multiLang_joint )
eng_test_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=["*"], exGroups=multiLang_joint, exResults=multiLang_joint, sort=True )

eng_grp.to_csv('summary/bf16-eng-summary.csv', index=False)
eng_test.to_csv('summary/bf16-eng-results.csv', index=False)
eng_test_sorted.to_csv('summary/bf16-sorted-eng-results.csv', index=False)
eng_grp_sorted.to_csv('summary/bf16-sorted-eng-summary.csv', index=False)

# English focused subset
eng_focus_mixed=["lambada_openai", "lambada_standard", "blimp", "piqa", "copa", "sciq", "truthfulqa", "pythia"] #"np_open", "cmmlu", "record"
eng_focus_tGrps=["anli", "glue", "mmlu" ]
eng_focus_tTest=["blimp", "arc_*", "logiqa", "winogrande", "openbookqa", "hellaswag"]

eng_focus_tGrps = eng_focus_tGrps + eng_focus_mixed
eng_focus_tTest = eng_focus_tTest + eng_focus_mixed

eng_focus = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=eng_focus_tGrps, inResults=eng_focus_tTest )
eng_focus_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=eng_focus_tGrps, inResults=eng_focus_tTest, sort=True )
eng_focus.to_csv('summary/bf16-eng-focus.csv', index=False)
eng_focus_sorted.to_csv('summary/bf16-sorted-eng-focus.csv', index=False)

# RWKV perf tracking
rwkv_eng_focus_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=eng_focus_tGrps, inResults=eng_focus_tTest, exModels=[], inModels=FOCUS_MODEL_LIST, sort=True, simplified=True )
rwkv_eng_focus_sorted.to_csv('summary/rwkv-x-dev-bf16-sorted-eng-focus.csv', index=False)

# RWKV perf tracking
rwkv_eng_all_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=["*"], exModels=[], inModels=FOCUS_MODEL_LIST, sort=True, simplified=True )
rwkv_eng_all_sorted.to_csv('summary/rwkv-x-dev-bf16-sorted-eng-all.csv', index=False)

# # Overall results
# rwkv_all_results = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=["*"], inModels=["./rwkv-x-dev/*", "rwkv-x-dev/*", "RWKV/*"], exModels=[], sort=True )
# rwkv_all_results.to_csv('summary/rwkv-x-dev-bf16-all-results-and-groups.csv', index=False)

# List the files
!ls -lh summary

total 38760
-rw-r--r--@ 1 picocreator  staff   1.4M Aug 12 16:40 bf16-all-results-and-groups.csv
-rw-r--r--@ 1 picocreator  staff   373K Aug 12 16:40 bf16-all-simplified-results-and-groups.csv
-rw-r--r--@ 1 picocreator  staff   373K Aug 12 16:40 bf16-all-sorted-results-and-groups.csv
-rw-r--r--@ 1 picocreator  staff    99K Aug 12 16:40 bf16-eng-focus.csv
-rw-r--r--@ 1 picocreator  staff   1.3M Aug 12 16:40 bf16-eng-results.csv
-rw-r--r--@ 1 picocreator  staff   113K Aug 12 16:40 bf16-eng-summary.csv
-rw-r--r--@ 1 picocreator  staff   142K Aug 12 16:40 bf16-multilang-results.csv
-rw-r--r--@ 1 picocreator  staff    20K Aug 12 16:40 bf16-multilang-summary.csv
-rw-r--r--@ 1 picocreator  staff    99K Aug 12 16:40 bf16-sorted-eng-focus.csv
-rw-r--r--@ 1 picocreator  staff   1.3M Aug 12 16:40 bf16-sorted-eng-results.csv
-rw-r--r--@ 1 picocreator  staff   113K Aug 12 16:40 bf16-sorted-eng-summary.csv
-rw-r--r--@ 1 picocreator  staff    20K Aug 12 16:40 bf16-sorted-multilang-summary.csv
-rw-r--

In [7]:
# 21 eval focus
focus_21=["sciq", "glue", "anli", "mnli", "mnli_mismatch", "swag", "winogrande", "wnli", "truthfulqa", "logiqa", "logiqa2", "lambada_standard", "lambada_openai", "mmlu", "piqa", "arc_easy", "arc_challenge", "hellaswag", "openbookqa", "mathqa", "arithmetic"]
focus_21_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=focus_21, inResults=focus_21, exModels=[], inModels=["./rwkv-x-dev/*", "rwkv-x-dev/*", "RWKV/*", "meta-llama/Llama-2-7b*", "mistralai/Mistral-7B-v0.1"], sort=True, simplified=True )
focus_21_sorted.to_csv('summary/rwkv-x-dev-bf16-sorted-eng-21-focus.csv', index=False)

# English 180
eng_180=[
    "anli",
    "glue",
    "blimp",
    "truthfulqa",
    "lambada",
    "ai2_arc",
    "multimedqa",
    "pythia",
    "mathqa",
    "mmlu",
    "anli_r1",
    "anli_r2",
    "anli_r3",
    "wsc",
    "lambada_standard_cloze_yaml",
    "mnli",
    "mnli_mismatch",
    "mrpc",
    "qnli",
    "qqp",
    "rte",
    "sst2",
    "wnli",
    "blimp_adjunct_island",
    "blimp_anaphor_gender_agreement",
    "blimp_anaphor_number_agreement",
    "blimp_animate_subject_passive",
    "blimp_animate_subject_trans",
    "blimp_causative",
    "blimp_complex_NP_island",
    "blimp_coordinate_structure_constraint_complex_left_branch",
    "blimp_coordinate_structure_constraint_object_extraction",
    "blimp_determiner_noun_agreement_1",
    "blimp_determiner_noun_agreement_2",
    "blimp_determiner_noun_agreement_irregular_1",
    "blimp_determiner_noun_agreement_irregular_2",
    "blimp_determiner_noun_agreement_with_adj_2",
    "blimp_determiner_noun_agreement_with_adj_irregular_1",
    "blimp_determiner_noun_agreement_with_adj_irregular_2",
    "blimp_determiner_noun_agreement_with_adjective_1",
    "blimp_distractor_agreement_relational_noun",
    "blimp_distractor_agreement_relative_clause",
    "blimp_drop_argument",
    "blimp_ellipsis_n_bar_1",
    "blimp_ellipsis_n_bar_2",
    "blimp_existential_there_object_raising",
    "blimp_existential_there_quantifiers_1",
    "blimp_existential_there_quantifiers_2",
    "blimp_existential_there_subject_raising",
    "blimp_expletive_it_object_raising",
    "blimp_inchoative",
    "blimp_intransitive",
    "blimp_irregular_past_participle_adjectives",
    "blimp_irregular_past_participle_verbs",
    "blimp_irregular_plural_subject_verb_agreement_1",
    "blimp_irregular_plural_subject_verb_agreement_2",
    "blimp_left_branch_island_echo_question",
    "blimp_left_branch_island_simple_question",
    "blimp_matrix_question_npi_licensor_present",
    "blimp_npi_present_1",
    "blimp_npi_present_2",
    "blimp_only_npi_licensor_present",
    "blimp_only_npi_scope",
    "blimp_passive_1",
    "blimp_passive_2",
    "blimp_principle_A_c_command",
    "blimp_principle_A_case_1",
    "blimp_principle_A_case_2",
    "blimp_principle_A_domain_1",
    "blimp_principle_A_domain_2",
    "blimp_principle_A_domain_3",
    "blimp_principle_A_reconstruction",
    "blimp_regular_plural_subject_verb_agreement_1",
    "blimp_regular_plural_subject_verb_agreement_2",
    "blimp_sentential_negation_npi_licensor_present",
    "blimp_sentential_negation_npi_scope",
    "blimp_sentential_subject_island",
    "blimp_superlative_quantifiers_1",
    "blimp_superlative_quantifiers_2",
    "blimp_tough_vs_raising_1",
    "blimp_tough_vs_raising_2",
    "blimp_transitive",
    "blimp_wh_island",
    "blimp_wh_questions_object_gap",
    "blimp_wh_questions_subject_gap",
    "blimp_wh_questions_subject_gap_long_distance",
    "blimp_wh_vs_that_no_gap",
    "blimp_wh_vs_that_no_gap_long_distance",
    "blimp_wh_vs_that_with_gap",
    "blimp_wh_vs_that_with_gap_long_distance",
    "sciq",
    "truthfulqa_mc1",
    "truthfulqa_mc2",
    "multirc",
    "lambada_openai",
    "lambada_standard",
    "piqa",
    "prost",
    "wsc273",
    "qa4mre_2011",
    "qa4mre_2012",
    "qa4mre_2013",
    "arc_challenge",
    "arc_easy",
    "logiqa",
    "winogrande",
    "boolq",
    "logiqa2",
    "openbookqa",
    "medmcqa",
    "medqa_4options",
    "mmlu_anatomy",
    "mmlu_clinical_knowledge",
    "mmlu_college_biology",
    "mmlu_college_medicine",
    "mmlu_medical_genetics",
    "mmlu_professional_medicine",
    "pubmedqa",
    "mc_taco",
    "lambada_openai_mt_de",
    "lambada_openai_mt_en",
    "lambada_openai_mt_es",
    "lambada_openai_mt_fr",
    "lambada_openai_mt_it",
    "mmlu_formal_logic",
    "mmlu_high_school_european_history",
    "mmlu_high_school_us_history",
    "mmlu_high_school_world_history",
    "mmlu_international_law",
    "mmlu_jurisprudence",
    "mmlu_logical_fallacies",
    "mmlu_moral_disputes",
    "mmlu_moral_scenarios",
    "mmlu_philosophy",
    "mmlu_prehistory",
    "mmlu_professional_law",
    "mmlu_world_religions",
    "mmlu_business_ethics",
    "mmlu_global_facts",
    "mmlu_human_aging",
    "mmlu_management",
    "mmlu_marketing",
    "mmlu_miscellaneous",
    "mmlu_nutrition",
    "mmlu_professional_accounting",
    "mmlu_virology",
    "mmlu_econometrics",
    "mmlu_high_school_geography",
    "mmlu_high_school_government_and_politics",
    "mmlu_high_school_macroeconomics",
    "mmlu_high_school_microeconomics",
    "mmlu_high_school_psychology",
    "mmlu_human_sexuality",
    "mmlu_professional_psychology",
    "mmlu_public_relations",
    "mmlu_security_studies",
    "mmlu_sociology",
    "mmlu_us_foreign_policy",
    "mmlu_abstract_algebra",
    "mmlu_astronomy",
    "mmlu_college_chemistry",
    "mmlu_college_computer_science",
    "mmlu_college_mathematics",
    "mmlu_college_physics",
    "mmlu_computer_security",
    "mmlu_conceptual_physics",
    "mmlu_electrical_engineering",
    "mmlu_elementary_mathematics",
    "mmlu_high_school_biology",
    "mmlu_high_school_chemistry",
    "mmlu_high_school_computer_science",
    "mmlu_high_school_mathematics",
    "mmlu_high_school_physics",
    "mmlu_high_school_statistics",
    "mmlu_machine_learning",
    "wic",
    "swag",
    "hellaswag",
    "cb",
    "sglue_rte"
]
eng_180_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=eng_180, inResults=eng_180, exModels=[], inModels=["./rwkv-x-dev/*", "rwkv-x-dev/*", "RWKV/*", "meta-llama/Llama-2-7b*", "mistralai/Mistral-7B-v0.1"], sort=True, simplified=True )
eng_180_sorted.to_csv('summary/rwkv-x-dev-bf16-sorted-eng-180.csv', index=False)

